Import libraries, config

In [1]:
from bs4 import BeautifulSoup
import requests
from pathlib import Path
import time
import random

Create lists with edibility symbols

In [ ]:
elements = ['🟢!','🟢','🟡🟢','🟡','🔴','🔴☠']

edible = ['🟢!','🟢']
non_edible = ['🟡🟢','🟡']
deadly = ['🔴','🔴☠']

Create 2 lists:
* mushroom names (in format 'Amanita_echinocephala')
* mushroom webpages (in format 'https://grzyby.pl/pelna/gatunki/Amanita_echinocephala')

In [3]:
# Credentials to use full page functionality
credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
URL_init = "https://www.grzyby.pl/logowanie"

# Log in using credential
form_data = credentials
s = requests.Session()
server = s.post(URL_init, data = form_data)

# Get full list of species
URL = 'https://www.grzyby.pl/pelna/gatunki/'
page = s.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

mushroom_names = []
mushroom_webs = []
for item in soup.find_all('td'):
    if item.find('a', href = True) and '_' in str(item) and '-' not in str(item):
        name = item.find('a').text
        name_clean = item.find('a').text.replace('.htm', '')
        if len(name_clean.split('_')) == 2:
            mushroom_webs.append('https://grzyby.pl/pelna/gatunki/'+name)
            mushroom_names.append(name_clean)

In [27]:
# Check
print(len(mushroom_names))
print(len(mushroom_webs))

4927
4927


Create mushroom dictionary

In [14]:
# name - number of expected dictionaries
# l_names - list with mushroom names
# l_webs - list with mushroom websites

def mushroom_dict_init(name:str,l_names:list,l_webs:list):
    try:
        mushroom_dict_name = {l_names[i]: {'edible': None, 'web': l_webs[i], 'img' : []} for i in range(len(l_names))}
        print(f'Created mushroom_dict_{name} with {len(mushroom_dict_name)} elements.')
        return  mushroom_dict_name

    except Exception as e:
        print(f'ERROR - not possible to create dictionary: {e}.')

In [53]:
mushroom_dict_01 = mushroom_dict_init('01',mushroom_names,mushroom_webs)
mushroom_dict_clean = mushroom_dict_init('clean',mushroom_names,mushroom_webs)
mushroom_dict_copy = mushroom_dict_init('copy',mushroom_names,mushroom_webs)

Created mushroom_dict_01 with 4927 elements.
Created mushroom_dict_clean with 4927 elements.
Created mushroom_dict_copy with 4927 elements.


Short dictionary (Amanita, Boletus, Tricholoma) for further tests

In [22]:
short_list = ['Amanita','Boletus','Tricholoma']

In [23]:
# name - name of dictionary
# l_names - list with mushroom names
# l_webs - list with mushroom websites
# l_mushs - list with expected families to be included in final dictionary

def mushroom_dict_short_init(name:str,l_names:list,l_webs:list, l_mushs:list):
    l_names_short = []
    l_webs_short = []

    try:
        for mushroom_name in l_names:
            for elmnt in l_mushs:
                if elmnt in mushroom_name:
                    l_names_short.append(mushroom_name)

        for mushroom_web in l_webs:
            for elmnt in l_mushs:
                if elmnt in mushroom_web:
                    l_webs_short.append(mushroom_web)

        mushroom_dict_short_name = {l_names_short[i]: {'edible': None, 'web': l_webs_short[i], 'img' : []} for i in range(len(l_names_short))}
        print(f'Created mushroom_dict_short_{name} with {len(mushroom_dict_short_name)} elements.')
        return mushroom_dict_short_name

    except Exception as e:
        print(f'ERROR - not possible to create dictionary: {e}.')

In [51]:
mushroom_dict_short_01 = mushroom_dict_short_init('01',mushroom_names,mushroom_webs,short_list)
mushroom_dict_short_clean = mushroom_dict_short_init('clean',mushroom_names,mushroom_webs,short_list)
mushroom_dict_short_copy = mushroom_dict_short_init('copy',mushroom_names,mushroom_webs,short_list)

Created mushroom_dict_short_01 with 127 elements.
Created mushroom_dict_short_clean with 127 elements.
Created mushroom_dict_short_copy with 127 elements.


In [50]:
# x - sleep time (s)
# dict_1 - dictionary to clean
# dict_2 - copy of dict_1

def dict_edibility_cleanup(x:int,dict1:dict, dict2:dict):
    elements = ['🟢!','🟢','🟡🟢','🟡','🔴','🔴☠']

    try:
        for key, value in dict2.items():
            URL = value['web']
            page = ''

            while page == '':
                try:
                    page = requests.get(URL)
                    break
                except:
                    print('Connection refused by the server.')
                    print(f'{x} sec break.')
                    time.sleep(x)
                    print('Continue...')
                    continue

            soup = BeautifulSoup(page.content, "html.parser")

            try:
                y = random.randint(5,15)
                print(f'Starting with {key} ({list(dict2.keys()).index(key)+1}/{len(dict2)}).')
                edibility = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

                if edibility not in elements:
                    del dict1[key]
                    print(f'>>>>>{key} removed. Mushrooms in clean dictionary: {len(dict1)}/{len(dict2)}. Break for {y} sec.')

                else:
                    dict1[key]['edible'] = edibility
                    print(f'>>>>>Edibility {edibility} added for: {key}. Break for {y} sec.')

                time.sleep(y)

            except Exception as e1:
                z = random.randint(5,15)
                print(f'Error:{str(e1)}. Break for {z} sec.')
                time.sleep(z)

        print('*************************')
        print(f'Clean up done! Mushrooms in clean dictionary: {len(dict1)}')
        print('*************************')

    except Exception as e2:
        print(f'Error:{str(e2)}.')

In [54]:
mushroom_dict_01 = mushroom_dict_init('01',mushroom_names,mushroom_webs)
mushroom_dict_clean = mushroom_dict_init('clean',mushroom_names,mushroom_webs)
mushroom_dict_copy = mushroom_dict_init('copy',mushroom_names,mushroom_webs)

Created mushroom_dict_01 with 4927 elements.
Created mushroom_dict_clean with 4927 elements.
Created mushroom_dict_copy with 4927 elements.


In [ ]:
dict_edibility_cleanup(7,mushroom_dict_clean,mushroom_dict_copy)

Starting with Abortiporus_biennis (1/4927).
>>>>>Abortiporus_biennis removed. Mushrooms in clean dictionary: 4926/4927. Break for 10 sec.
Starting with Abortiporus_fractipes (2/4927).
>>>>>Abortiporus_fractipes removed. Mushrooms in clean dictionary: 4925/4927. Break for 7 sec.
Starting with Absconditella_celata (3/4927).
>>>>>Absconditella_celata removed. Mushrooms in clean dictionary: 4924/4927. Break for 9 sec.
Starting with Absconditella_delutula (4/4927).
>>>>>Absconditella_delutula removed. Mushrooms in clean dictionary: 4923/4927. Break for 15 sec.
Starting with Absconditella_fossarum (5/4927).
>>>>>Absconditella_fossarum removed. Mushrooms in clean dictionary: 4922/4927. Break for 10 sec.
Starting with Absconditella_lignicola (6/4927).
>>>>>Absconditella_lignicola removed. Mushrooms in clean dictionary: 4921/4927. Break for 9 sec.
Starting with Absconditella_pauxilla (7/4927).
>>>>>Absconditella_pauxilla removed. Mushrooms in clean dictionary: 4920/4927. Break for 14 sec.
Start

In [52]:
dict_edibility_cleanup(5,mushroom_dict_short_clean,mushroom_dict_short_copy)

Starting with Amanita_argentea (1/127).
>>>>>Amanita_argentea removed. Mushrooms in clean dictionary: 126/127. Break for 9 sec.
Starting with Amanita_battarae (2/127).
>>>>>Edibility 🟢 added for: Amanita_battarae. Break for 12 sec.
Starting with Amanita_caesarea (3/127).
>>>>>Edibility 🟢! added for: Amanita_caesarea. Break for 7 sec.
Starting with Amanita_ceciliae (4/127).
>>>>>Amanita_ceciliae removed. Mushrooms in clean dictionary: 125/127. Break for 11 sec.


KeyboardInterrupt: 

In [197]:
def photo_search(x:int, dict1:dict):
    photos_count = 0
    # Credentials
    credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
    URL_init = "https://www.grzyby.pl/logowanie"

    # Log in using credential
    form_data = credentials
    s = requests.Session()
    server = s.post(URL_init, data = form_data)

    try:
        for key, value in dict1.items():
            URL = value['web']
            page = ''

            while page == '':
                try:
                    page = s.get(URL)
                    break
                except:
                    print('Connection refused by the server.')
                    print(f'{x} sec break.')
                    time.sleep(x)
                    print('Continue...')
                    continue

            soup = BeautifulSoup(page.content, "html.parser")
            latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])


            try:
                print(f'Starting with {key} ({list(dict1.keys()).index(key)+1}/{len(dict1)}).')
                for item in soup.find_all('img'):

                    if latin_name in str(item['alt']) and 'mapa' not in str(item['src']) and 'icon' not in str(item['src']):
                        value['img'].append(('https://www.grzyby.pl'+item['src']))

                photos_count += len(dict1[key]['img'])
                print(f'{len(dict1[key]["img"])} photos found.')
                time.sleep(random.randint(1,5))

            except Exception as e1:
                print(f'Error: {str(e1)}.')
                time.sleep(random.randint(1,5))

        print('*************************')
        print(f'{photos_count} photos found!')
        print('*************************')

    except Exception as e2:
        print(f'Error:{str(e2)}.')

In [189]:
photo_search(7,mushroom_dict_short_clean)

Starting with Amanita_battarae (1/69).
Starting with Amanita_caesarea (2/69).
Starting with Amanita_citrina (3/69).
Starting with Amanita_crocea (4/69).
Starting with Amanita_decipiens (5/69).
Starting with Amanita_eliae (6/69).
Starting with Amanita_franchetii (7/69).
Starting with Amanita_fulva (8/69).
Starting with Amanita_gemmata (9/69).
Starting with Amanita_mairei (10/69).
Starting with Amanita_muscaria (11/69).
Starting with Amanita_nivalis (12/69).
Starting with Amanita_pantherina (13/69).
Starting with Amanita_phalloides (14/69).
Starting with Amanita_porphyria (15/69).
Starting with Amanita_regalis (16/69).
Starting with Amanita_rubescens (17/69).
Starting with Amanita_spissa (18/69).
Starting with Amanita_strobiliformis (19/69).
Starting with Amanita_submembranacea (20/69).
Starting with Amanita_vaginata (21/69).
Connection refused by the server.
7 sec break.
Continue...
Starting with Amanita_verna (22/69).
Starting with Amanita_virosa (23/69).
Starting with Boletus_aereus (

Scratchbook

In [168]:
# remove items w/o edibility from dictionary

for key, value in mushroom_dict_short_copy.items():
    URL = value['web']
    page = ''

    while page == '':
        try:
            page = requests.get(URL)
            break
        except:
            print('Connection refused by the server.')
            print(f'{x} sec break.')
            time.sleep(x)
            print('Continue...')
            continue

    soup = BeautifulSoup(page.content, "html.parser")

    try:
        print(f'Starting with {key} ({list(mushroom_dict_short_copy.keys()).index(key)+1}/{len(mushroom_dict_short_copy)}).')
        edibility = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

        if edibility not in elements:
            del mushroom_dict_short_clean[key]
            print(f'{key} removed. Mushrooms left:{len(mushroom_dict_short_clean)}/{len(mushroom_dict_short_copy)}.')

        else:
            mushroom_dict_short_clean[key]['edible'] = edibility
            print(f'Edibility added for:{key}.')

        time.sleep(random.randint(1,5))


    except Exception as e1:
        print(f'Error:{str(e1)}.')
        time.sleep(random.randint(1,5))

Starting with Amanita_argentea (0/127).
Error:'Amanita_argentea'.
Starting with Amanita_battarae (1/127).
Edibility added for:Amanita_battarae.
Starting with Amanita_caesarea (2/127).
Edibility added for:Amanita_caesarea.
Starting with Amanita_ceciliae (3/127).
Error:'Amanita_ceciliae'.
Starting with Amanita_citrina (4/127).
Edibility added for:Amanita_citrina.


KeyboardInterrupt: 

In [26]:
# Remove elements with non-described edibility - SHORT
for key, value in mushroom_dict_amanita_clean_copy.items():
    URL = value['web']
    page = requests.get(URL, timeout = 5)
    soup = BeautifulSoup(page.content, "html.parser")

    latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])
    edibility = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

    if edibility not in elements:
        del mushroom_dict_amanita_clean[key]
    else:
        mushroom_dict_amanita_clean[key]['edible'] = edibility

In [ ]:
# Get latin name from website
# >> sometimes there is mismatch between page name and latin name (title), used in alt (alternative text)
URL = "https://www.grzyby.pl/pelna/gatunki/Psilocybe_semilanceata.htm"
page = s.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])

In [34]:
# EDIBLE - AWESOME
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Boletus_edulis.htm"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'})#.find('a')#.get_text().split()[0]

<div class="w3-display-container w3-padding" id="tytul-blok">
<div class="w3-hide-large w3-hide-medium w3-small w3-display-topleft w3-text-gray" style="margin-left:4px"><b>grzyby.pl</b></div>
<div class="w3-small" style="padding-top:8px"><a href="/oatlasie.htm">O atlasie »</a></div><h1>przeciążenie</h1>
</div>

In [47]:
# DEADLY
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Amanita_phalloides.htm"
page = s.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

'🔴☠'

In [48]:
# NON_EDIBLE
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Hygrophoropsis_aurantiaca.htm"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

'🟡🟢'

In [49]:
# NON_EDIBLE
# Get edible/poisonous feature from the website
URL = "https://www.grzyby.pl/pelna/gatunki/Tylopilus_felleus.htm"
page = requests.get(URL)
soup = BeautifulSoup(page.content, "html.parser")

soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]

'🟡'

In [40]:
elements = ['🟢!','🟢','🟡🟢','🟡','🔴','🔴☠']

edible = ['🟢!','🟢']
non_edible = ['🟡🟢','🟡']
deadly = ['🔴','🔴☠']

In [ ]:
# Get all images sources from website
# URL = "https://www.grzyby.pl/pelna/gatunki/Psilocybe_semilanceata.htm"
# page = s.get(URL)
# soup = BeautifulSoup(page.content, "html.parser")
#
# for item in soup.find_all('img'):
#     if 'Psilocybe semilanceata' in str(item['alt']) and 'mapa'not in str(item['src']) and 'icon'not in str(item['src']):
#         print('https://www.grzyby.pl'+item['src'])

In [28]:
# # Add images to dictionary - SHORT
# # Credentials
# credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
# URL_init = "https://www.grzyby.pl/logowanie"
#
# # Log in using credential
# form_data = credentials
# s = requests.Session()
# server = s.post(URL_init, data = form_data)
#
# # Add images to dict
# for key, value in mushroom_dict_amanita_clean.items():
#     URL = value['web']
#     page = s.get(URL, timeout = 3)
#     soup = BeautifulSoup(page.content, "html.parser")
#     latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])
#
#     for item in soup.find_all('img'):
#         if latin_name in str(item['alt']) and 'mapa'not in str(item['src']) and 'icon'not in str(item['src']):
#             value['img'].append(('https://www.grzyby.pl'+item['src']))

In [ ]:
-- https://www.google.com/search?safe=off&site=&tbm=isch&source=hp&q=amanita-muscaria-mushroom&oq=amanita-muscaria-mushroom&gs_l=img

In [286]:
# # Version for full dict (~5000 elements)
# # Find edible/non-edible/poisonous/deadly tags
# elements = []
# for key, value in mushroom_dict.items():
#     URL = value['web']
#     page = requests.get(URL, timeout = 10)
#     soup = BeautifulSoup(page.content, "html.parser")
#
#     try:
#         if (soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text().split()[0]) not in elements:
#             el1 = soup.find('div', {'id' : 'tytul-blok'}).find('a').get_text()
#             el2 = el1.split()
#             el3 = el2[0]
#             elements.append(el3)
#     except:
#         print('error:',get.error())

C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: I

error


C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'grzyby.pl'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
C:\Users\User\anaconda3\lib\site-packages\urllib3\connectionpool.py:1045: I

In [217]:
# Add images to dictionary - TEST
# Credentials
credentials = dict(l.rstrip().split('=') for l in open('config.properties') if not l.startswith("#"))
URL_init = "https://www.grzyby.pl/logowanie"

# Log in using credential
form_data = credentials
s = requests.Session()
server = s.post(URL_init, data = form_data)

# Add images to dict
for key, value in mushroom_dict_short.items():
    URL = value['web']
    page = s.get(URL)
    soup = BeautifulSoup(page.content, "html.parser")
    latin_name = ' '.join(soup.find('title').text.split(' ')[0:2])

    for item in soup.find_all('img'):
        if latin_name in str(item['alt']) and 'mapa'not in str(item['src']) and 'icon'not in str(item['src']):
            value['img'].append(('https://www.grzyby.pl'+item['src']))

In [220]:
# Check
for key, value in mushroom_dict_short.items():
    if len(value['img']) != 0:
        print(key)
        print(value['edible'])
        print(value['web'])
        print(value['img'])

Boletopsis_leucomelaena
p
https://grzyby.pl/pelna/gatunki/Boletopsis_leucomelaena.htm
['https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276439ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276440ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276441ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276442ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276443ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402936ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402937ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402938ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-184257-402939ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276439ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276440ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276441ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-276442ss.jpg', 'https://www.grzyby.pl/pelna/foto/GREJ/GREJ-146176-2764